# Binary Classification Example

The Spark MLlib Pipelines API provides higher-level API built on top of DataFrames for constructing ML pipelines.
You can read more about the Pipelines API in the [MLlib programming guide](https://spark.apache.org/docs/latest/ml-guide.html).

**Binary Classification** is the task of predicting a binary label.
For example, is an email spam or not spam? Should I show this ad to this user or not? Will it rain tomorrow or not?
This notebook illustrates algorithms for making these types of predictions.

## Dataset Review

The Adult dataset is publicly available at the [UCI Machine Learning Repository](https://archive.ics.uci.edu/ml/datasets/Adult).
This data derives from census data and consists of information about 48842 individuals and their annual income.
You can use this information to predict if an individual earns **<=50K or >50k** a year.
The dataset consists of both numeric and categorical variables.

Attribute Information:

- age: continuous
- workclass: Private,Self-emp-not-inc, Self-emp-inc, Federal-gov, Local-gov, State-gov, Without-pay, Never-worked
- fnlwgt: continuous
- education: Bachelors, Some-college, 11th, HS-grad, Prof-school, Assoc-acdm, Assoc-voc...
- education-num: continuous
- marital-status: Married-civ-spouse, Divorced, Never-married, Separated, Widowed, Married-spouse-absent...
- occupation: Tech-support, Craft-repair, Other-service, Sales, Exec-managerial, Prof-specialty, Handlers-cleaners...
- relationship: Wife, Own-child, Husband, Not-in-family, Other-relative, Unmarried
- race: White, Asian-Pac-Islander, Amer-Indian-Eskimo, Other, Black
- sex: Female, Male
- capital-gain: continuous
- capital-loss: continuous
- hours-per-week: continuous
- native-country: United-States, Cambodia, England, Puerto-Rico, Canada, Germany...

Target/Label: - <=50K, >50K

## Load Data

The Adult dataset is available in databricks-datasets. Read in the data using the CSV data source for Spark and rename the columns appropriately.

In [0]:
%fs ls databricks-datasets/adult/adult.data

path name size dbfs:/databricks-datasets/adult/adult.data adult.data 3974305

In [0]:
%fs head databricks-datasets/adult/adult.data

[Truncated to first 65536 bytes]
39, State-gov, 77516, Bachelors, 13, Never-married, Adm-clerical, Not-in-family, White, Male, 2174, 0, 40, United-States, <=50K
50, Self-emp-not-inc, 83311, Bachelors, 13, Married-civ-spouse, Exec-managerial, Husband, White, Male, 0, 0, 13, United-States, <=50K
38, Private, 215646, HS-grad, 9, Divorced, Handlers-cleaners, Not-in-family, White, Male, 0, 0, 40, United-States, <=50K
53, Private, 234721, 11th, 7, Married-civ-spouse, Handlers-cleaners, Husband, Black, Male, 0, 0, 40, United-States, <=50K
28, Private, 338409, Bachelors, 13, Married-civ-spouse, Prof-specialty, Wife, Black, Female, 0, 0, 40, Cuba, <=50K
37, Private, 284582, Masters, 14, Married-civ-spouse, Exec-managerial, Wife, White, Female, 0, 0, 40, United-States, <=50K
49, Private, 160187, 9th, 5, Married-spouse-absent, Other-service, Not-in-family, Black, Female, 0, 0, 16, Jamaica, <=50K
52, Self-emp-not-inc, 209642, HS-grad, 9, Married-civ-spouse, Exec-managerial, Husband, White, Male, 0, 0, 45, United-States, >50K
31, Private, 45781, Masters, 14, Never-married, Prof-specialty, Not-in-family, White, Female, 14084, 0, 50, United-States, >50K
42, Private, 159449, Bachelors, 13, Married-civ-spouse, Exec-managerial, Husband, White, Male, 5178, 0, 40, United-States, >50K
37, Private, 280464, Some-college, 10, Married-civ-spouse, Exec-managerial, Husband, Black, Male, 0, 0, 80, United-States, >50K
30, State-gov, 141297, Bachelors, 13, Married-civ-spouse, Prof-specialty, Husband, Asian-Pac-Islander, Male, 0, 0, 40, India, >50K
23, Private, 122272, Bachelors, 13, Never-married, Adm-clerical, Own-child, White, Female, 0, 0, 30, United-States, <=50K
32, Private, 205019, Assoc-acdm, 12, Never-married, Sales, Not-in-family, Black, Male, 0, 0, 50, United-States, <=50K
40, Private, 121772, Assoc-voc, 11, Married-civ-spouse, Craft-repair, Husband, Asian-Pac-Islander, Male, 0, 0, 40, ?, >50K
34, Private, 245487, 7th-8th, 4, Married-civ-spouse, Transport-moving, Husband, Amer-Indian-Eskimo, Male, 0, 0, 45, Mexico, <=50K
25, Self-emp-not-inc, 176756, HS-grad, 9, Never-married, Farming-fishing, Own-child, White, Male, 0, 0, 35, United-States, <=50K
32, Private, 186824, HS-grad, 9, Never-married, Machine-op-inspct, Unmarried, White, Male, 0, 0, 40, United-States, <=50K
38, Private, 28887, 11th, 7, Married-civ-spouse, Sales, Husband, White, Male, 0, 0, 50, United-States, <=50K
43, Self-emp-not-inc, 292175, Masters, 14, Divorced, Exec-managerial, Unmarried, White, Female, 0, 0, 45, United-States, >50K
40, Private, 193524, Doctorate, 16, Married-civ-spouse, Prof-specialty, Husband, White, Male, 0, 0, 60, United-States, >50K
54, Private, 302146, HS-grad, 9, Separated, Other-service, Unmarried, Black, Female, 0, 0, 20, United-States, <=50K
35, Federal-gov, 76845, 9th, 5, Married-civ-spouse, Farming-fishing, Husband, Black, Male, 0, 0, 40, United-States, <=50K
43, Private, 117037, 11th, 7, Married-civ-spouse, Transport-moving, Husband, White, Male, 0, 2042, 40, United-States, <=50K
59, Private, 109015, HS-grad, 9, Divorced, Tech-support, Unmarried, White, Female, 0, 0, 40, United-States, <=50K
56, Local-gov, 216851, Bachelors, 13, Married-civ-spouse, Tech-support, Husband, White, Male, 0, 0, 40, United-States, >50K
19, Private, 168294, HS-grad, 9, Never-married, Craft-repair, Own-child, White, Male, 0, 0, 40, United-States, <=50K
54, ?, 180211, Some-college, 10, Married-civ-spouse, ?, Husband, Asian-Pac-Islander, Male, 0, 0, 60, South, >50K
39, Private, 367260, HS-grad, 9, Divorced, Exec-managerial, Not-in-family, White, Male, 0, 0, 80, United-States, <=50K
49, Private, 193366, HS-grad, 9, Married-civ-spouse, Craft-repair, Husband, White, Male, 0, 0, 40, United-States, <=50K
23, Local-gov, 190709, Assoc-acdm, 12, Never-married, Protective-serv, Not-in-family, White, Male, 0, 0, 52, United-States, <=50K
20, Private, 266015, Some-college, 10, Never-married, Sales, Own-child, Black, Male, 0, 0, 44, United-States, <=50K
45, Private, 386940, Bachelors, 13, Di

In [0]:
from pyspark.sql.types import DoubleType, StringType, StructField, StructType

schema = StructType([
  StructField("age", DoubleType(), False),
  StructField("workclass", StringType(), False),
  StructField("fnlwgt", DoubleType(), False),
  StructField("education", StringType(), False),
  StructField("education_num", DoubleType(), False),
  StructField("marital_status", StringType(), False),
  StructField("occupation", StringType(), False),
  StructField("relationship", StringType(), False),
  StructField("race", StringType(), False),
  StructField("sex", StringType(), False),
  StructField("capital_gain", DoubleType(), False),
  StructField("capital_loss", DoubleType(), False),
  StructField("hours_per_week", DoubleType(), False),
  StructField("native_country", StringType(), False),
  StructField("income", StringType(), False)
])

dataset = spark.read.format("csv").schema(schema).load("/databricks-datasets/adult/adult.data")
cols = dataset.columns

In [0]:
display(dataset)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income 39.0 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United-States <=50K 50.0 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United-States <=50K 38.0 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United-States <=50K 53.0 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United-States <=50K 28.0 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K 37.0 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United-States <=50K 49.0 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K 52.0 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United-States >50K 31.0 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United-States >50K 42.0 Private 159449.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 5178.0 0.0 40.0 United-States >50K 37.0 Private 280464.0 Some-college 10.0 Married-civ-spouse Exec-managerial Husband Black Male 0.0 0.0 80.0 United-States >50K 30.0 State-gov 141297.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Husband Asian-Pac-Islander Male 0.0 0.0 40.0 India >50K 23.0 Private 122272.0 Bachelors 13.0 Never-married Adm-clerical Own-child White Female 0.0 0.0 30.0 United-States <=50K 32.0 Private 205019.0 Assoc-acdm 12.0 Never-married Sales Not-in-family Black Male 0.0 0.0 50.0 United-States <=50K 40.0 Private 121772.0 Assoc-voc 11.0 Married-civ-spouse Craft-repair Husband Asian-Pac-Islander Male 0.0 0.0 40.0 ? >50K 34.0 Private 245487.0 7th-8th 4.0 Married-civ-spouse Transport-moving Husband Amer-Indian-Eskimo Male 0.0 0.0 45.0 Mexico <=50K 25.0 Self-emp-not-inc 176756.0 HS-grad 9.0 Never-married Farming-fishing Own-child White Male 0.0 0.0 35.0 United-States <=50K 32.0 Private 186824.0 HS-grad 9.0 Never-married Machine-op-inspct Unmarried White Male 0.0 0.0 40.0 United-States <=50K 38.0 Private 28887.0 11th 7.0 Married-civ-spouse Sales Husband White Male 0.0 0.0 50.0 United-States <=50K 43.0 Self-emp-not-inc 292175.0 Masters 14.0 Divorced Exec-managerial Unmarried White Female 0.0 0.0 45.0 United-States >50K 40.0 Private 193524.0 Doctorate 16.0 Married-civ-spouse Prof-specialty Husband White Male 0.0 0.0 60.0 United-States >50K 54.0 Private 302146.0 HS-grad 9.0 Separated Other-service Unmarried Black Female 0.0 0.0 20.0 United-States <=50K 35.0 Federal-gov 76845.0 9th 5.0 Married-civ-spouse Farming-fishing Husband Black Male 0.0 0.0 40.0 United-States <=50K 43.0 Private 117037.0 11th 7.0 Married-civ-spouse Transport-moving Husband White Male 0.0 2042.0 40.0 United-States <=50K 59.0 Private 109015.0 HS-grad 9.0 Divorced Tech-support Unmarried White Female 0.0 0.0 40.0 United-States <=50K 56.0 Local-gov 216851.0 Bachelors 13.0 Married-civ-spouse Tech-support Husband White Male 0.0 0.0 40.0 United-States >50K 19.0 Private 168294.0 HS-grad 9.0 Never-married Craft-repair Own-child White Male 0.0 0.0 40.0 United-States <=50K 54.0 ? 180211.0 Some-college 10.0 Married-civ-spouse ? Husband Asian-Pac-Islander Male 0.0 0.0 60.0 South >50K 39.0 Private 367260.0 HS-grad 9.0 Divorced Exec-managerial Not-in-family White Male 0.0 0.0 80.0 United-States <=50K 49.0 Private 193366.0 HS-grad 9.0 Married-civ-spouse Craft-repair Husband White Male 0.0 0.0 40.0 United-States <=50K 23.0 Local-gov 190709.0 Assoc-acdm 12.0 Never-married Protective-serv Not-in-family White Male 0.0 0.0 52.0 United-States <=50K 20.0 Private 266015.0 Some-college 10.0 Never-married Sales Own-child Black Male 0.0 0.0 44.0

## Preprocess Data

To use algorithms like Logistic Regression, you must first convert the categorical variables in the dataset into numeric variables.
There are two ways to do this.

* Category Indexing

  This is basically assigning a numeric value to each category from {0, 1, 2, ...numCategories-1}.
  This introduces an implicit ordering among your categories, and is more suitable for ordinal variables (eg: Poor: 0, Average: 1, Good: 2)

* One-Hot Encoding

  This converts categories into binary vectors with at most one nonzero value (eg: (Blue: [1, 0]), (Green: [0, 1]), (Red: [0, 0]))

This notebook uses a combination of [StringIndexer] and, depending on your Spark version, either [OneHotEncoder] or [OneHotEncoderEstimator] to convert the categorical variables.
`OneHotEncoder` and `OneHotEncoderEstimator` return a [SparseVector]. 

Since there is more than one stage of feature transformations, use a [Pipeline] to tie the stages together.
This simplifies the code.

[StringIndexer]: http://spark.apache.org/docs/latest/ml-features.html#stringindexer
[OneHotEncoderEstimator]: https://spark.apache.org/docs/2.4.5/api/python/pyspark.ml.html?highlight=one%20hot%20encoder#pyspark.ml.feature.OneHotEncoderEstimator
[SparseVector]: https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.ml.linalg.SparseVector.html#pyspark.ml.linalg.SparseVector
[Pipeline]: https://spark.apache.org/docs/latest/ml-pipeline.html#ml-pipelines
[OneHotEncoder]: https://spark.apache.org/docs/latest/ml-features.html#onehotencoder

In [0]:
import pyspark
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, VectorAssembler

from distutils.version import LooseVersion

categoricalColumns = ["workclass", "education", "marital_status", "occupation", "relationship", "race", "sex", "native_country"]
stages = [] # stages in Pipeline
for categoricalCol in categoricalColumns:
    # Category Indexing with StringIndexer
    stringIndexer = StringIndexer(inputCol=categoricalCol, outputCol=categoricalCol + "Index")
    # Use OneHotEncoder to convert categorical variables into binary SparseVectors
    if LooseVersion(pyspark.__version__) < LooseVersion("3.0"):
        from pyspark.ml.feature import OneHotEncoderEstimator
        encoder = OneHotEncoderEstimator(inputCols=[stringIndexer.getOutputCol()], outputCols=[categoricalCol + "classVec"])
    else:
        from pyspark.ml.feature import OneHotEncoder
        encoder = OneHotEncoder(inputCols=[stringIndexer.getOutputCol()], outputCols=[categoricalCol + "classVec"])
    # Add stages.  These are not run here, but will run all at once later on.
    stages += [stringIndexer, encoder]

In [0]:
print(pyspark.__version__)

3.1.2


In [0]:
LooseVersion(pyspark.__version__)

Out[5]: LooseVersion ('3.1.2')

The above code basically indexes each categorical column using the `StringIndexer`,
and then converts the indexed categories into one-hot encoded variables.
The resulting output has the binary vectors appended to the end of each row.

Use the `StringIndexer` again to encode labels to label indices.

In [0]:
# Convert label into label indices using the StringIndexer
label_stringIdx = StringIndexer(inputCol="income", outputCol="label")
stages += [label_stringIdx]

Use a `VectorAssembler` to combine all the feature columns into a single vector column.
This includes both the numeric columns and the one-hot encoded binary vector columns in the dataset.

In [0]:
# Transform all features into a vector using VectorAssembler
numericCols = ["age", "fnlwgt", "education_num", "capital_gain", "capital_loss", "hours_per_week"]
assemblerInputs = [c + "classVec" for c in categoricalColumns] + numericCols
assembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")
stages += [assembler]

Run the stages as a Pipeline. This puts the data through all of the feature transformations in a single call.

In [0]:
from pyspark.ml.classification import LogisticRegression
  
partialPipeline = Pipeline().setStages(stages)
pipelineModel = partialPipeline.fit(dataset)
preppedDataDF = pipelineModel.transform(dataset)

In [0]:
# Fit model to prepped data
lrModel = LogisticRegression().fit(preppedDataDF)

# ROC for training data
display(lrModel, preppedDataDF, "ROC")

False Positive Rate True Positive Rate Threshold 0.0 0.0 0.9999999999999981 0.0 0.029411764705882353 0.9999999999999981 0.0 0.058823529411764705 0.9990711228185274 0.0 0.08823529411764706 0.998799388244511 0.0 0.11764705882352941 0.9980956262870607 0.0 0.14705882352941177 0.9924488810180737 0.0 0.17647058823529413 0.9857871527075162 0.0 0.20588235294117646 0.9780074377264764 0.0 0.23529411764705882 0.9625272519799214 0.0 0.2647058823529412 0.8880880030405891 0.0 0.29411764705882354 0.8669953699778059 0.0 0.3235294117647059 0.841326881247684 0.0 0.35294117647058826 0.8370708257511488 0.0 0.38235294117647056 0.8296623044091199 0.0 0.4117647058823529 0.7909014579505567 0.01098901098901099 0.4117647058823529 0.7891036172588488 0.01098901098901099 0.4411764705882353 0.7233834160971737 0.01098901098901099 0.47058823529411764 0.7219383873566756 0.01098901098901099 0.5 0.7143957689542965 0.01098901098901099 0.5294117647058824 0.7123894418945409 0.01098901098901099 0.5588235294117647 0.6786024854520709 0.01098901098901099 0.5882352941176471 0.6688699173930381 0.01098901098901099 0.6176470588235294 0.6213988126053775 0.01098901098901099 0.6470588235294118 0.5871356395526401 0.02197802197802198 0.6470588235294118 0.582992091188786 0.02197802197802198 0.6764705882352942 0.5587515702487251 0.02197802197802198 0.7058823529411765 0.5461912925736032 0.02197802197802198 0.7352941176470589 0.5263363696374029 0.03296703296703297 0.7352941176470589 0.5260220627350953 0.04395604395604396 0.7352941176470589 0.4924699600417892 0.054945054945054944 0.7352941176470589 0.4495253649734853 0.06593406593406594 0.7352941176470589 0.4462019135692611 0.07692307692307693 0.7352941176470589 0.44485567385948066 0.07692307692307693 0.7647058823529411 0.44027682844389293 0.07692307692307693 0.7941176470588235 0.4390507172380286 0.08791208791208792 0.7941176470588235 0.43703321579289234 0.08791208791208792 0.8235294117647058 0.4279460622836938 0.0989010989010989 0.8235294117647058 0.41995303742701984 0.0989010989010989 0.8529411764705882 0.36640191948470513 0.10989010989010989 0.8529411764705882 0.3552702456863094 0.12087912087912088 0.8529411764705882 0.34609818277412285 0.13186813186813187 0.8529411764705882 0.3444438928891447 0.13186813186813187 0.8823529411764706 0.34407807125707324 0.14285714285714285 0.8823529411764706 0.32660142330467323 0.15384615384615385 0.8823529411764706 0.31927715779178323 0.16483516483516483 0.8823529411764706 0.3186130928838401 0.17582417582417584 0.8823529411764706 0.31054843561782086 0.18681318681318682 0.8823529411764706 0.3010508994150498 0.1978021978021978 0.8823529411764706 0.29166054241797323 0.2087912087912088 0.8823529411764706 0.2899373620547263 0.2087912087912088 0.9117647058823529 0.28484144837434533 0.2087912087912088 0.9411764705882353 0.28432482548474225 0.21978021978021978 0.9411764705882353 0.26227539170753644 0.23076923076923078 0.9411764705882353 0.2499789726975744 0.24175824175824176 0.9411764705882353 0.2457635615100061 0.25274725274725274 0.9411764705882353 0.24558281101476587 0.26373626373626374 0.9411764705882353 0.2407117220905335 0.26373626373626374 0.9705882352941176 0.19108727692254213 0.27472527472527475 0.9705882352941176 0.1562462264286013 0.2857142857142857 0.9705882352941176 0.1356705266637186 0.2967032967032967 0.9705882352941176 0.13124547689108046 0.3076923076923077 0.9705882352941176 0.10788923703961839 0.31868131868131866 0.9705882352941176 0.10371200218164067 0.31868131868131866 1.0 0.0872556169941322 0.32967032967032966 1.0 0.08525437904355049 0.34065934065934067 1.0 0.08456538438360905 0.3516483516483517 1.0 0.08369401106537322 0.3626373626373626 1.0 0.07634713901821144 0.37362637362637363 1.0 0.07053831520389298 0.38461538461538464 1.0 0.06942492237717712 0.3956043956043956 1.0 0.060255889514018834 0.4065934065934066 1.0 0.05981059572332226 0.4175824175824176 1.0 0.05954492589579985 0.42857142857142855 1.0 0.053149458715173736 0.43956043956043955 1.0 0.05184149246871561 0.45054945054945056 1

In [0]:
display(lrModel, preppedDataDF)

fitted values residuals -2.3931829353970278 -0.08369401106537322 -1.1223113099359612 -0.24558281101476587 -0.030122437287170123 -0.4924699600417892 -2.347613929426214 0.9127443830058678 -1.1213359560759493 -0.2457635615100061 -5.3062962400000355 -0.0049357815848263265 -2.493045750440344 -0.07634713901821144 -5.16303436772777 -0.005691722515687392 -0.5959524881147853 -0.3552702456863094 0.7473567948921191 0.3213975145479291 -4.731060836836686 -0.008740050549433276 -2.578449544749006 -0.07053831520389298 -2.759632794790879 -0.05954492589579985 -3.426420772331019 -0.03147987613083092 -0.6435526820666233 -0.3444438928891447 -3.658715901005307 -0.02511838730122573 -0.7235968546438196 -0.32660142330467323 -0.8873328386062227 -0.29166054241797323 -2.381873927410644 -0.08456538438360905 -0.7570956780588123 -0.31927715779178323 1.3195307037453823 -0.7891036172588488 33.90358722562088 1.887379141862766E-15 -4.325474998117228 -0.013054589158705499 -4.4859563827256475 -0.011140596496495236 -5.394452356631649 -0.004521173110207166 -0.7975565657784511 -0.31054843561782086 -0.2025885972285021 -0.4495253649734853 -3.2264017242546843 -0.038184178496829424 3.245948430183283 0.037472748020078606 -3.553040783481504 -0.027840156463344146 -4.2636090745351725 -0.013876168358177399 -4.336085620679074 -0.012918584113183695 1.6365930929216004 0.16292917424885123 0.9168300620868777 0.28560423104570354 3.79481295732249 0.02199256227352364 -1.442960757846955 0.8089127230774579 -2.7470072964539773 -0.060255889514018834 -0.5476839394513251 0.6335980805152949 0.9613070206154265 0.2766165839028263 -6.3806280590115305 -0.0016911936723565946 0.10418238146421566 -0.5260220627350953 -3.3962118407754165 -0.032414064007325605 -6.735315941905414 -0.0011867895956715335 -0.8422985706078712 -0.3010508994150498 -3.3538440035736277 -0.0337695126197981 -4.078561854759706 -0.01664988602110473 -5.6463143188902665 -0.0035180845253244275 -1.6864275770897328 -0.1562462264286013 -3.3239732000562268 -0.03475786196608577 -3.3454450092940355 -0.03404464026412213 -3.8246967837543058 -0.02135889327673146 -1.8517246825578897 -0.1356705266637186 -0.7601527986765323 -0.3186130928838401 -2.7548985176085043 -0.05981059572332226 4.239294167349501 0.014212847292483843 -3.9531501292212203 -0.018832665547164562 -0.9205715646654785 0.7151585516256547 -4.6502861966854425 -0.009468359049592534 -6.862688818023491 -0.0010450042060689002 0.9540970818322803 0.2780616126433244 -5.89703145233665 -0.0027400605132802403 0.9070173945829272 0.2876105581054591 1.5832358445118473 0.17033769559088008 -4.809402148130507 -0.0080868028280906 -4.814328291327889 -0.00804738383248138 0.3350684329514758 -0.582992091188786 6.9806047241237685 9.288771814726093E-4 -0.25321142765684745 -0.43703321579289234 -3.417661083767392 -0.03174804823054933 0.23609690660853866 0.4412484297512749 0.7030783008771504 0.33113008260696186 -5.022532093819453 -0.006544709186587672 0.10544306516056023 0.47366363036259707 -7.965388065070378 -3.4715635743853834E-4 2.071358019600361 0.1119119969594109 -4.3147570358465535 -0.013193404329202796 0.4954897110715984 0.37860118739462245 -5.461154898446589 -0.004230671529149799 -5.314195816202718 -0.004897134791833402 4.8784797441577945 0.007551118981926286 -0.9231090608621878 0.7156751745152578 0.18529350711690373 0.4538087074263968 -1.034175530348073 -0.26227539170753644 -0.6451731878465563 0.6559219287429268 -3.1954143808758673 -0.03933865289081384 -3.2893208396407294 -0.035939369833570156 -3.1816000230194694 -0.039864048115210826 -2.373006534815794 -0.08525437904355049 1.874649696674164 0.1330046300221941 -1.0987244374254115 -0.2499789726975744 -2.9063308487801613 -0.05184149246871561 -2.942784179793099 -0.05007866152835494 -0.24501556095881927 0.5609492827619714 -3.3559259986299423 -0.0337016448300268 -3.261740678028254 -0.036907286754479185 -0.8956882818661671 -0.2899373620547263 -9.217823087574095 -9.924467053989972E-5 -5.914786159354563 -0.0026919706770092144 -1.8899911642260905 -0.1312454

In [0]:
# Keep relevant columns
selectedcols = ["label", "features"] + cols
dataset = preppedDataDF.select(selectedcols)
display(dataset)

label features age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(4, 10, 24, 32, 44, 48, 52, 53, 94, 95, 96, 97, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 39.0, 77516.0, 13.0, 2174.0, 40.0)) 39.0 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United-States <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(1, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 50.0, 83311.0, 13.0, 13.0)) 50.0 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United-States <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 8, 25, 38, 44, 48, 52, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 38.0, 215646.0, 9.0, 40.0)) 38.0 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United-States <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 13, 23, 38, 43, 49, 52, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 53.0, 234721.0, 7.0, 40.0)) 53.0 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United-States <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 10, 23, 29, 47, 49, 62, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 28.0, 338409.0, 13.0, 40.0)) 28.0 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 11, 23, 31, 47, 48, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 284582.0, 14.0, 40.0)) 37.0 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United-States <=50K 0.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 18, 28, 34, 44, 49, 64, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 49.0, 160187.0, 5.0, 16.0)) 49.0 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K 1.0 Map(vectorType -> sparse, length -> 100, indices -> List(1, 8, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 52.0, 209642.0, 9.0, 45.0)) 52.0 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United-States >50K 1.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 11, 24, 29, 44, 48, 53, 94, 95, 96, 97, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 31.0, 45781.0, 14.0, 14084.0, 50.0)) 31.0 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United-States >50K 1.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 97, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 42.0, 159449.0, 13.0, 5178.0, 40.0)) 42.0 Private 159449.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 5178.0 0.0 40.0 United-States >50K 1.0 Map(vectorType -> sparse, length -> 100, indices -> List(0, 9, 23, 31, 43, 49, 52, 53, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 280464.0, 10.0, 80.0)) 37.0 Private 280464.0 Some-college 10.0 Married-civ-spouse Exec-managerial Husband Black Male 0.0 0.0 80.0 United-States >50K 1.0 Map(vectorType -> sparse, length -> 100, indices -> List(4, 10, 23, 29, 43, 50, 52, 61, 94, 95, 96, 99), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 30.0, 141297.0, 13.0, 40.0)) 30.0 State-gov 141297.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Husband Asian-Pac-Islander Male 0.0 0.0 40.0 India >50K 0.0 Map(vectorType -> sparse, lengt

In [0]:
### Randomly split data into training and test sets. set seed for reproducibility
(trainingData, testData) = dataset.randomSplit([0.7, 0.3], seed=100)
print(trainingData.count())
print(testData.count())

22832
9729

## Fit and Evaluate Models

Now, try out some of the Binary Classification algorithms available in the Pipelines API.

Out of these algorithms, the below are also capable of supporting multiclass classification with the Python API:
- Decision Tree Classifier
- Random Forest Classifier

These are the general steps to build the models:
- Create initial model using the training set
- Tune parameters with a `ParamGrid` and 5-fold Cross Validation
- Evaluate the best model obtained from the Cross Validation using the test set

Use the `BinaryClassificationEvaluator` to evaluate the models, which uses [areaUnderROC] as the default metric.

[areaUnderROC]: https://en.wikipedia.org/wiki/Receiver_operating_characteristic#Area_under_the_curve

## Logistic Regression

You can read more about [Logistic Regression] from the [classification and regression] section of MLlib Programming Guide.
In the Pipelines API, you can now perform Elastic-Net Regularization with Logistic Regression, as well as other linear methods.

[classification and regression]: https://spark.apache.org/docs/latest/ml-classification-regression.html
[Logistic Regression]: https://spark.apache.org/docs/latest/ml-classification-regression.html#logistic-regression

In [0]:
from pyspark.ml.classification import LogisticRegression

# Create initial LogisticRegression model
lr = LogisticRegression(labelCol="label", featuresCol="features", maxIter=10)

# Train model with Training Data
lrModel = lr.fit(trainingData)

In [0]:
# Make predictions on test data using the transform() method.
# LogisticRegression.transform() will only use the 'features' column.
predictions = lrModel.transform(testData)

In [0]:
# View model's predictions and probabilities of each prediction class
# You can select any columns in the above schema to view as well
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.16304404160706326, 0.8369559583929367)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7011865325539305, 0.2988134674460695)) 32.0 Prof-specialty 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4980113187669919, 0.5019886812330081)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.68126165186417, 0.31873834813583)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6108620507115975, 0.3891379492884025)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6096341652357697, 0.39036583476423026)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6002598383118382, 0.39974016168816184)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5998980983235114, 0.4001019016764886)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7478554516614605, 0.2521445483385395)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9885496846452969, 0.011450315354703089)) 20.0 Prof-specialty 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.39744646947264645, 0.6025535305273535)) 35.0 Prof-specialty 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4647425466787711, 0.5352574533212289)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5319870434427573, 0.46801295655724273)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7178970558249936, 0.28210294417500636)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6266900055359131, 0.37330999446408686)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7099589063976993, 0.2900410936023007)) 27.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5536768741720968, 0.44632312582790323)) 32.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4172251178125425, 0.5827748821874574)) 45.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5214727652172715, 0.4785272347827285)) 46.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.3821667669429044, 0.6178332330570956)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.610793143850439, 0.38920685614956096)) 25.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6215439716806245, 0.3784560283193755)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5674194890993921, 0.4325805109006079)) 34.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4001056077226381, 0.5998943922773619)) 37.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.2962302832339926, 0.7037697167660074)) 41.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4807773491760785, 0.5192226508239215)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8665236881089899, 0.13347631189101006)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8354480928433033, 0.16455190715669665)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8676712303941271, 0.13232876960587292)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8107982039621157, 0.18920179603788434)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8334896632368821, 0.16651033676311788)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.817842205826383, 0.182157794173617)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.77818724090187

Use `BinaryClassificationEvaluator` to evaluate the model.

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator

# Evaluate model
evaluator = BinaryClassificationEvaluator()
evaluator.evaluate(predictions)

Out[14]: 0.8993574699928725

Note that the default metric for the ``BinaryClassificationEvaluator`` is ``areaUnderROC``

In [0]:
evaluator.getMetricName()

Out[15]: 'areaUnderROC'

The evaluator accepts two kinds of metrics - areaUnderROC and areaUnderPR.
Set it to areaUnderPR by using evaluator.setMetricName("areaUnderPR").

Now, tune the model using `ParamGridBuilder` and `CrossValidator`.

You can use `explainParams()` to print a list of all parameters and their definitions.

In [0]:
print(lr.explainParams())

aggregationDepth: suggested depth for treeAggregate (>= 2). (default: 2)
elasticNetParam: the ElasticNet mixing parameter, in range [0, 1]. For alpha = 0, the penalty is an L2 penalty. For alpha = 1, it is an L1 penalty. (default: 0.0)
family: The name of family which is a description of the label distribution to be used in the model. Supported options: auto, binomial, multinomial (default: auto)
featuresCol: features column name. (default: features, current: features)
fitIntercept: whether to fit an intercept term. (default: True)
labelCol: label column name. (default: label, current: label)
lowerBoundsOnCoefficients: The lower bounds on coefficients if fitting under bound constrained optimization. The bound matrix must be compatible with the shape (1, number of features) for binomial regression, or (number of classes, number of features) for multinomial regression. (undefined)
lowerBoundsOnIntercepts: The lower bounds on intercepts if fitting under bound constrained optimization. The bounds vector size must beequal with 1 for binomial regression, or the number oflasses for multinomial regression. (undefined)
maxBlockSizeInMB: maximum memory in MB for stacking input data into blocks. Data is stacked within partitions. If more than remaining data size in a partition then it is adjusted to the data size. Default 0.0 represents choosing optimal value, depends on specific algorithm. Must be >= 0. (default: 0.0)
maxIter: max number of iterations (>= 0). (default: 100, current: 10)
predictionCol: prediction column name. (default: prediction)
probabilityCol: Column name for predicted class conditional probabilities. Note: Not all models output well-calibrated probability estimates! These probabilities should be treated as confidences, not precise probabilities. (default: probability)
rawPredictionCol: raw prediction (a.k.a. confidence) column name. (default: rawPrediction)
regParam: regularization parameter (>= 0). (default: 0.0)
standardization: whether to standardize the training features before fitting the model. (default: True)
threshold: Threshold in binary classification prediction, in range [0, 1]. If threshold and thresholds are both set, they must match.e.g. if threshold is p, then thresholds must be equal to [1-p, p]. (default: 0.5)
thresholds: Thresholds in multi-class classification to adjust the probability of predicting each class. Array must have length equal to the number of classes, with values > 0, excepting that at most one value may be 0. The class with largest value p/t is predicted, where p is the original probability of that class and t is the class's threshold. (undefined)
tol: the convergence tolerance for iterative algorithms (>= 0). (default: 1e-06)
upperBoundsOnCoefficients: The upper bounds on coefficients if fitting under bound constrained optimization. The bound matrix must be compatible with the shape (1, number of features) for binomial regression, or (number of classes, number of features) for multinomial regression. (undefined)
upperBoundsOnIntercepts: The upper bounds on intercepts if fitting under bound constrained optimization. The bound vector size must be equal with 1 for binomial regression, or the number of classes for multinomial regression. (undefined)
weightCol: weight column name. If this is not set or empty, we treat all instance weights as 1.0. (undefined)

Using three values for regParam, three values for maxIter, and two values for elasticNetParam,
the grid includes 3 x 3 x 3 = 27 parameter settings for CrossValidator.

In [0]:
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

# Create ParamGrid for Cross Validation
paramGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.01, 0.5, 2.0])
             .addGrid(lr.elasticNetParam, [0.0, 0.5, 1.0])
             .addGrid(lr.maxIter, [1, 5, 10])
             .build())

In [0]:
# Create 5-fold CrossValidator
cv = CrossValidator(estimator=lr, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)

# Run cross validations
cvModel = cv.fit(trainingData)
# this will likely take a fair amount of time because of the amount of models that we're creating and testing

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [0]:
# Use the test set to measure the accuracy of the model on new data
predictions = cvModel.transform(testData)

In [0]:
# cvModel uses the best model found from the Cross Validation
# Evaluate best model
evaluator.evaluate(predictions)

Out[20]: 0.8977643264031809

You can also access the model's feature weights and intercepts.

In [0]:
print('Model Intercept: ', cvModel.bestModel.intercept)

Model Intercept: -1.3832039720849316

In [0]:
weights = cvModel.bestModel.coefficients
weights = [(float(w),) for w in weights]  # convert numpy type to float, and to tuple
weightsDF = sqlContext.createDataFrame(weights, ["Feature Weight"])
display(weightsDF)

Feature Weight -0.281603275704831 -0.6264483359096494 -0.4360275569860984 -0.5064247711709583 -0.506326689118052 -0.004948144171750953 0.07086989623963032 -2.66978938102928 -0.5593567014148134 -0.22394378958134853 0.5737091727046981 0.8976634297736545 -0.02732965272147547 -1.2761244527152253 -0.042220243675365664 -1.2432064202100166 -1.7513331537893073 1.269765487533909 -1.4918049429191638 -0.7975316495227874 1.34153256909672 -1.442990991365734 -1.5518469838399462 0.5226994331763453 -1.024441666149217 -0.4768837489957835 -0.540408982596901 -0.21970565980915377 -0.5019992096484727 0.300719176096832 -0.1747572052680891 0.5258894794470769 -0.23198908371013502 0.04304739973547087 -1.1024291505844745 -0.5317982977746302 -0.5170654863613252 -0.28580749630497504 -0.8710796747405309 -0.9632982847987452 0.39537943576708084 0.190916900434488 -1.6012498241539617 0.35650768782678394 -0.19669674210265467 -1.1996652296244663 -0.6140843310837796 1.1380763779390815 -0.5091342868672956 -0.7098265623215485 -0.4456188577927626 -0.9780774814011537 0.4572454065930687 -0.6751200901903649 -1.6089114180872437 -0.9075041056722982 -0.4903094088309559 -0.30700225210883925 -0.44377364611780984 -1.8852995707285332 -1.5352582213953891 -1.3494803252434868 -0.5754855838198739 -0.3836723107533862 -1.1113918586114049 -1.529709148940378 -1.3375911856922502 -0.061300379719 -2.4753279050524033 -1.7520286036633481 -1.0240075339499934 -0.018423977523275622 -0.8517697891691116 -2.7555518372546692 -0.9225099409268483 -0.6357985457421316 -0.5669713517696919 -0.5868262599748618 -1.588239222171451 -1.7903481479053778 -0.31334908199533845 -1.7060095723566793 -1.4240083459112733 -0.18557464826230746 -0.3170664091107644 -0.4728232339844238 -1.0510910779600922 -0.6546723240661646 -0.34549137330732355 -0.434979519004375 -2.673064786676108 -1.2359989216910454 -0.8449859637738643 -1.2145318347622336 0.01535191763729664 3.6390051160148775E-7 -0.026882725709490955 1.2636600493120225E-4 5.338623834712852E-4 0.020804294256713506

In [0]:
# View best model's predictions and probabilities of each prediction class
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.2329641926839113, 0.7670358073160887)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6552066745246206, 0.34479332547537944)) 32.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5391022452506109, 0.4608977547493891)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6373416944642422, 0.36265830553575784)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6016034358099771, 0.3983965641900229)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5947767904063128, 0.4052232095936872)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5899376739565122, 0.4100623260434878)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5976373681713757, 0.4023626318286243)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6907455609652081, 0.3092544390347919)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.957840027974627, 0.04215997202537303)) 20.0 Prof-specialty 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.46810434624054026, 0.5318956537594597)) 35.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5225067439383878, 0.4774932560616122)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.555207325707806, 0.44479267429219405)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6710300723456664, 0.32896992765433364)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6186038529781688, 0.3813961470218312)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7019637858830454, 0.2980362141169546)) 27.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6322053845193183, 0.3677946154806817)) 32.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5498670106804634, 0.4501329893195366)) 45.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6040351425207384, 0.3959648574792616)) 46.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5193649069810575, 0.48063509301894247)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5898672495855667, 0.4101327504144333)) 25.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5984004293217614, 0.4015995706782386)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5529163721062962, 0.4470836278937038)) 34.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.44880050671940264, 0.5511994932805974)) 37.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.37057275936993206, 0.6294272406300679)) 41.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4939388859549916, 0.5060611140450084)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8233597236299156, 0.1766402763700844)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7854251544595204, 0.21457484554047956)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.814123097262339, 0.185876902737661)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7661980772624881, 0.23380192273751188)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7823681679644525, 0.21763183203554748)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7759524346009257, 0.22404756539907433)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.75416722415408

## Decision Trees

You can read more about [Decision Trees](http://spark.apache.org/docs/latest/mllib-decision-tree.html) in the Spark MLLib Programming Guide.
The Decision Trees algorithm is popular because it handles categorical
data and works out of the box with multiclass classification tasks.

In [0]:
from pyspark.ml.classification import DecisionTreeClassifier

# Create initial Decision Tree Model
dt = DecisionTreeClassifier(labelCol="label", featuresCol="features", maxDepth=3)

# Train model with Training Data
dtModel = dt.fit(trainingData)

You can extract the number of nodes in the decision tree as well as the
tree depth of the model.

In [0]:
print("numNodes = ", dtModel.numNodes)
print("depth = ", dtModel.depth)

numNodes = 11
depth = 3

In [0]:
display(dtModel)

treeNode {"index":5,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0],"feature":23,"overflow":false} {"index":1,"featureType":"continuous","prediction":null,"threshold":7792.0,"categories":null,"feature":97,"overflow":false} {"index":0,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":3,"featureType":"continuous","prediction":null,"threshold":20.5,"categories":null,"feature":94,"overflow":false} {"index":2,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":4,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":9,"featureType":"continuous","prediction":null,"threshold":12.5,"categories":null,"feature":96,"overflow":false} {"index":7,"featureType":"continuous","prediction":null,"threshold":3368.0,"categories":null,"feature":97,"overflow":false} {"index":6,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":8,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":10,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false}

In [0]:
# Make predictions on test data using the Transformer.transform() method.
predictions = dtModel.transform(testData)

In [0]:
predictions.printSchema()

root
-- label: double (nullable = false)
-- features: vector (nullable = true)
-- age: double (nullable = true)
-- workclass: string (nullable = true)
-- fnlwgt: double (nullable = true)
-- education: string (nullable = true)
-- education_num: double (nullable = true)
-- marital_status: string (nullable = true)
-- occupation: string (nullable = true)
-- relationship: string (nullable = true)
-- race: string (nullable = true)
-- sex: string (nullable = true)
-- capital_gain: double (nullable = true)
-- capital_loss: double (nullable = true)
-- hours_per_week: double (nullable = true)
-- native_country: string (nullable = true)
-- income: string (nullable = true)
-- rawPrediction: vector (nullable = true)
-- probability: vector (nullable = true)
-- prediction: double (nullable = false)

In [0]:
# View model's predictions and probabilities of each prediction class
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 32.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 20.0 Prof-specialty 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.27598566308243727, 0.7240143369175627)) 35.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 27.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.27598566308243727, 0.7240143369175627)) 32.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.27598566308243727, 0.7240143369175627)) 45.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.27598566308243727, 0.7240143369175627)) 46.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.27598566308243727, 0.7240143369175627)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 25.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 34.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 37.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 41.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 0.2989507906014482)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7010492093985518, 

Evaluate the Decision Tree model with
`BinaryClassificationEvaluator`.

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator
# Evaluate model
evaluator = BinaryClassificationEvaluator()
evaluator.evaluate(predictions)

Out[30]: 0.7389268249816493

Entropy and the Gini coefficient are the supported measures of impurity for Decision Trees. This is ``Gini`` by default. Changing this value is simple, ``model.setImpurity("Entropy")``.

In [0]:
dt.getImpurity()

Out[31]: 'gini'

Now tune the model with using `ParamGridBuilder` and `CrossValidator`.

With three values for maxDepth and three values for maxBin, the grid has 3 x 3 = 9 parameter settings for `CrossValidator`.

In [0]:
# Create ParamGrid for Cross Validation
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
paramGrid = (ParamGridBuilder()
             .addGrid(dt.maxDepth, [1, 2, 6, 10])
             .addGrid(dt.maxBins, [20, 40, 80])
             .build())

In [0]:
# Create 5-fold CrossValidator
cv = CrossValidator(estimator=dt, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)

# Run cross validations
cvModel = cv.fit(trainingData)
# Takes ~5 minutes

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [0]:
print("numNodes = ", cvModel.bestModel.numNodes)
print("depth = ", cvModel.bestModel.depth)

numNodes = 485
depth = 10

In [0]:
# Use test set to measure the accuracy of the model on new data
predictions = cvModel.transform(testData)

In [0]:
# cvModel uses the best model found from the Cross Validation
# Evaluate best model
evaluator.evaluate(predictions)

Out[36]: 0.7556080515264616

In [0]:
# View Best model's predictions and probabilities of each prediction class
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5089285714285714, 0.49107142857142855)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8206106870229007, 0.17938931297709923)) 32.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8206106870229007, 0.17938931297709923)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9274193548387096, 0.07258064516129033)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 20.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7714285714285715, 0.22857142857142856)) 35.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7714285714285715, 0.22857142857142856)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7714285714285715, 0.22857142857142856)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7714285714285715, 0.22857142857142856)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 27.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8206106870229007, 0.17938931297709923)) 32.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 45.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 46.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6779661016949152, 0.3220338983050847)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 25.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4, 0.6)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5089285714285714, 0.49107142857142855)) 34.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5089285714285714, 0.49107142857142855)) 37.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5089285714285714, 0.49107142857142855)) 41.0 Craft-repair 0.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.0, 1.0)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9259259259259259, 0.07407407407407407)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9145077720207254, 0.08549222797927461)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7450980392156863, 0.2549019607843137)) 24.0 Craft-repair 0.0 0

## Random Forest

Random Forests uses an ensemble of trees to improve model accuracy.
You can read more about [Random Forest] from the [classification and regression] section of MLlib Programming Guide.

[classification and regression]: https://spark.apache.org/docs/latest/ml-classification-regression.html
[Random Forest]: https://spark.apache.org/docs/latest/ml-classification-regression.html#random-forests

In [0]:
from pyspark.ml.classification import RandomForestClassifier

# Create an initial RandomForest model.
rf = RandomForestClassifier(labelCol="label", featuresCol="features")

# Train model with Training Data
rfModel = rf.fit(trainingData)

In [0]:
# Make predictions on test data using the Transformer.transform() method.
predictions = rfModel.transform(testData)

In [0]:
predictions.printSchema()

root
-- label: double (nullable = false)
-- features: vector (nullable = true)
-- age: double (nullable = true)
-- workclass: string (nullable = true)
-- fnlwgt: double (nullable = true)
-- education: string (nullable = true)
-- education_num: double (nullable = true)
-- marital_status: string (nullable = true)
-- occupation: string (nullable = true)
-- relationship: string (nullable = true)
-- race: string (nullable = true)
-- sex: string (nullable = true)
-- capital_gain: double (nullable = true)
-- capital_loss: double (nullable = true)
-- hours_per_week: double (nullable = true)
-- native_country: string (nullable = true)
-- income: string (nullable = true)
-- rawPrediction: vector (nullable = true)
-- probability: vector (nullable = true)
-- prediction: double (nullable = false)

In [0]:
# View model's predictions and probabilities of each prediction class
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.537048668949202, 0.4629513310507979)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6776796783146757, 0.3223203216853244)) 32.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6524471509421086, 0.3475528490578914)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6783793074615304, 0.3216206925384696)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6524471509421086, 0.3475528490578914)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6783793074615304, 0.3216206925384696)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6783793074615304, 0.3216206925384696)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6854267291327509, 0.3145732708672492)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6783793074615304, 0.3216206925384696)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8385976167514594, 0.16140238324854073)) 20.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7429757356891866, 0.2570242643108133)) 35.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7429757356891866, 0.2570242643108133)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7429757356891866, 0.2570242643108133)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7500231573604071, 0.24997684263959283)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7500231573604071, 0.24997684263959283)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7424895109904129, 0.25751048900958706)) 27.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7164169713868287, 0.28358302861317136)) 32.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7171166005336833, 0.2828833994663166)) 45.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7171166005336833, 0.2828833994663166)) 46.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7171166005336833, 0.2828833994663166)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7424895109904129, 0.25751048900958706)) 25.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7260326591573598, 0.2739673408426401)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7171166005336833, 0.2828833994663166)) 34.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5649183163806137, 0.43508168361938615)) 37.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5649183163806137, 0.43508168361938615)) 41.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5989725001324517, 0.40102749986754826)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7495369326616335, 0.2504630673383666)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7424895109904129, 0.25751048900958706)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7495369326616335, 0.2504630673383666)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7123947341158026, 0.28760526588419744)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7424895109904129, 0.25751048900958706)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7424895109904129, 0.25751048900958706)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.71239473411

Evaluate the Random Forest model with `BinaryClassificationEvaluator`.

In [0]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator

# Evaluate model
evaluator = BinaryClassificationEvaluator()
evaluator.evaluate(predictions)

Out[42]: 0.8833054197207935

Now tune the model with `ParamGridBuilder` and `CrossValidator`.

With three values for maxDepth, two values for maxBin, and two values for numTrees,
the grid has 3 x 2 x 2 = 12 parameter settings for `CrossValidator`.

In [0]:
# Create ParamGrid for Cross Validation
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

paramGrid = (ParamGridBuilder()
             .addGrid(rf.maxDepth, [2, 4, 6])
             .addGrid(rf.maxBins, [20, 60])
             .addGrid(rf.numTrees, [5, 20])
             .build())

In [0]:
# Create 5-fold CrossValidator
cv = CrossValidator(estimator=rf, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)

# Run cross validations.  This can take about 6 minutes since it is training over 20 trees!
cvModel = cv.fit(trainingData)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [0]:
# Use the test set to measure the accuracy of the model on new data
predictions = cvModel.transform(testData)

In [0]:
# cvModel uses the best model found from the Cross Validation
# Evaluate best model
evaluator.evaluate(predictions)

Out[46]: 0.8910051255365896

In [0]:
# View Best model's predictions and probabilities of each prediction class
selected = predictions.select("label", "prediction", "probability", "age", "occupation")
display(selected)

label prediction probability age occupation 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5094807638277546, 0.49051923617224535)) 36.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.661701148411863, 0.338298851588137)) 32.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6475646101435547, 0.3524353898564453)) 33.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.661701148411863, 0.338298851588137)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6409016328210144, 0.3590983671789857)) 39.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.661701148411863, 0.338298851588137)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.661701148411863, 0.338298851588137)) 51.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6847313095078987, 0.31526869049210127)) 60.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6680692793701579, 0.331930720629842)) 34.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8630135705355219, 0.1369864294644781)) 20.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6519379453778007, 0.3480620546221994)) 35.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6581393246885289, 0.34186067531147113)) 42.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.662841208781064, 0.33715879121893594)) 43.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6751312798044983, 0.32486872019550184)) 48.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6751312798044983, 0.32486872019550184)) 50.0 Prof-specialty 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7574769856575871, 0.24252301434241294)) 27.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7159899688216296, 0.28401003117837054)) 32.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5498830605376097, 0.45011693946239034)) 45.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7159899688216296, 0.28401003117837054)) 46.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.552497439622577, 0.44750256037742303)) 56.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7574769856575871, 0.24252301434241294)) 25.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7928134317453115, 0.20718656825468856)) 28.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7159899688216296, 0.28401003117837054)) 34.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5276770357681291, 0.4723229642318709)) 37.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5667251253596969, 0.43327487464030306)) 41.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.591975169752973, 0.408024830247027)) 61.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7982240597646352, 0.20177594023536488)) 19.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7628876136769108, 0.23711238632308929)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7969683424845047, 0.20303165751549548)) 22.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7562677426937212, 0.24373225730627884)) 23.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7628876136769108, 0.23711238632308929)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7628876136769108, 0.23711238632308929)) 24.0 Craft-repair 0.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.756267742693721

## Make Predictions
As Random Forest gives the best areaUnderROC value, use the bestModel obtained from Random Forest for deployment,
and use it to generate predictions on new data.
Instead of new data, this example generates predictions on the entire dataset.

In [0]:
bestModel = cvModel.bestModel

In [0]:
# Generate predictions for entire dataset
finalPredictions = bestModel.transform(dataset)

In [0]:
# Evaluate best model
evaluator.evaluate(finalPredictions)

Out[50]: 0.8983753558281518

This example shows predictions grouped by age and occupation.

In [0]:
finalPredictions.createOrReplaceTempView("finalPredictions")

In an operational environment, analysts may use a similar machine learning pipeline to obtain predictions on new data, organize it into a table and use it for analysis or lead targeting.

In [0]:
%sql
SELECT occupation, prediction, count(*) AS count
FROM finalPredictions
GROUP BY occupation, prediction
ORDER BY occupation


occupation prediction count ? 0.0 1773 ? 1.0 70 Adm-clerical 1.0 175 Adm-clerical 0.0 3595 Armed-Forces 1.0 1 Armed-Forces 0.0 8 Craft-repair 0.0 3921 Craft-repair 1.0 178 Exec-managerial 0.0 2577 Exec-managerial 1.0 1489 Farming-fishing 1.0 70 Farming-fishing 0.0 924 Handlers-cleaners 0.0 1346 Handlers-cleaners 1.0 24 Machine-op-inspct 0.0 1963 Machine-op-inspct 1.0 39 Other-service 0.0 3277 Other-service 1.0 18 Priv-house-serv 0.0 148 Priv-house-serv 1.0 1 Prof-specialty 0.0 2433 Prof-specialty 1.0 1707 Protective-serv 0.0 579 Protective-serv 1.0 70 Sales 1.0 555 Sales 0.0 3095 Tech-support 0.0 819 Tech-support 1.0 109 Transport-moving 0.0 1547 Transport-moving 1.0 50

In [0]:
%sql
SELECT age, prediction, count(*) AS count
FROM finalPredictions
GROUP BY age, prediction
ORDER BY age

age prediction count 17.0 1.0 1 17.0 0.0 394 18.0 0.0 550 19.0 0.0 712 20.0 0.0 753 21.0 1.0 1 21.0 0.0 719 22.0 1.0 4 22.0 0.0 761 23.0 0.0 874 23.0 1.0 3 24.0 1.0 6 24.0 0.0 792 25.0 1.0 20 25.0 0.0 821 26.0 0.0 767 26.0 1.0 18 27.0 1.0 21 27.0 0.0 814 28.0 1.0 56 28.0 0.0 811 29.0 0.0 746 29.0 1.0 67 30.0 1.0 105 30.0 0.0 756 31.0 1.0 111 31.0 0.0 777 32.0 0.0 705 32.0 1.0 123 33.0 1.0 135 33.0 0.0 740 34.0 1.0 146 34.0 0.0 740 35.0 1.0 143 35.0 0.0 733 36.0 1.0 154 36.0 0.0 744 37.0 1.0 154 37.0 0.0 704 38.0 0.0 648 38.0 1.0 179 39.0 1.0 171 39.0 0.0 645 40.0 1.0 153 40.0 0.0 641 41.0 1.0 177 41.0 0.0 631 42.0 0.0 608 42.0 1.0 172 43.0 1.0 169 43.0 0.0 601 44.0 1.0 191 44.0 0.0 533 45.0 1.0 175 45.0 0.0 559 46.0 0.0 567 46.0 1.0 170 47.0 0.0 558 47.0 1.0 150 48.0 1.0 120 48.0 0.0 423 49.0 0.0 454 49.0 1.0 123 50.0 1.0 138 50.0 0.0 464 51.0 1.0 125 51.0 0.0 470 52.0 1.0 96 52.0 0.0 382 53.0 1.0 100 53.0 0.0 364 54.0 0.0 335 54.0 1.0 80 55.0 0.0 332 55.0 1.0 87 56.0 0.0 299 56.0 1.0 67 57.0 0.0 278 57.0 1.0 80 58.0 0.0 300 58.0 1.0 66 59.0 1.0 66 59.0 0.0 289 60.0 1.0 51 60.0 0.0 261 61.0 1.0 43 61.0 0.0 257 62.0 1.0 52 62.0 0.0 206 63.0 1.0 40 63.0 0.0 190 64.0 1.0 33 64.0 0.0 175 65.0 0.0 148 65.0 1.0 30 66.0 0.0 122 66.0 1.0 28 67.0 1.0 31 67.0 0.0 120 68.0 0.0 97 68.0 1.0 23 69.0 1.0 18 69.0 0.0 90 70.0 1.0 15 70.0 0.0 74 71.0 0.0 62 71.0 1.0 10 72.0 1.0 7 72.0 0.0 60 73.0 0.0 56 73.0 1.0 8 74.0 1.0 4 74.0 0.0 47 75.0 0.0 39 75.0 1.0 6 76.0 1.0 4 76.0 0.0 42 77.0 0.0 24 77.0 1.0 5 78.0 1.0 4 78.0 0.0 19 79.0 0.0 18 79.0 1.0 4 80.0 1.0 3 80.0 0.0 19 81.0 0.0 20 82.0 0.0 12 83.0 1.0 2 83.0 0.0 4 84.0 1.0 1 84.0 0.0 9 85.0 0.0 2 85.0 1.0 1 86.0 0.0 1 87.0 0.0 1 88.0 1.0 2 88.0 0.0 1 90.0 1.0 8 90.0 0.0 35